In [1]:
import os
os.chdir(path='../')

import numpy as np
import scanpy as sc
import pandas as pd
import STForte.helper as stfhelper
import plotly.express as px
trial_name = "trial-mouse_brain_coronal_Xenium"

import plotly.io as pio   
pio.kaleido.scope.mathjax = None

Global seed set to 0


In [2]:
adata = sc.read_h5ad(f"./{trial_name}/outputs/stforte.h5ad")
adata

AnnData object with n_obs × n_vars = 130557 × 248
    obs: 'cell_id', 'x_centroid', 'y_centroid', 'transcript_counts', 'control_probe_counts', 'control_codeword_counts', 'total_counts', 'cell_area', 'nucleus_area', 'n_counts', 'STForte_Mask', 'leiden', 'label_curated'
    var: 'gene_ids', 'feature_types', 'genome', 'n_cells'
    uns: 'leiden', 'log1p', 'neighbors', 'umap'
    obsm: 'STForte_ATTR', 'STForte_COMB', 'STForte_TOPO', 'X_umap', 'spatial'
    layers: 'count'
    obsp: 'connectivities', 'distances'

In [3]:
import plotly.express as px
from bokeh.themes import Theme
from bokeh.models import ColumnDataSource, LabelSet
from bokeh.layouts import column, row
from bokeh.plotting import curdoc, figure, show
from bokeh.transform import factor_cmap
from bokeh.io import output_notebook, export_svg, export_png
output_notebook()
plot_dir = f"./{trial_name}/plots"
if not os.path.exists(plot_dir):
    os.makedirs(plot_dir)

Loading BokehJS ...

In [4]:
color_curated = dict(zip(["1", "2", "4", "5", "8", "13", "14", "15", "17", "28", "30",
 "9", "10", "12", "20", "21", "0", "11", "16", "23", "26",
 "3", "7", "22", "24", "25", "6", "18", "19", "27", "29"
 ], 
stfhelper.pl.rgb2hex(px.colors.qualitative.Bold) + px.colors.qualitative.Plotly +\
    stfhelper.pl.rgb2hex(px.colors.qualitative.Vivid)[:10]))

In [5]:
leiden_isocortex = ["17", "1", "4", "5", "2", "14", "28"]
cat_isocortex = ['L1', 'L2/3', 'L4', 'L5', 'L6', 'L6b', 'C28']
adata_isocortex = adata[adata.obs['leiden'].apply(lambda x: True if x in leiden_isocortex else False), :]
label_isocortex = adata_isocortex.obs['leiden'].cat.rename_categories(dict(zip(leiden_isocortex, cat_isocortex)))
adata_isocortex.obs['label_isocortex'] = pd.Categorical(label_isocortex, categories=cat_isocortex)

gene_list = ['Gfap',  # L1
             'Rasgrf2',  # L2/3
             'Rorb',  # L4
             'Fezf2',  # L5
             'Rprm',  # L6
             'Ccn2',  # L6b
             'Nrep',  # RSP
             ][::-1]
fig = stfhelper.pl.plot_trend_genes(adata_isocortex, gene_list, 'label_isocortex',
                                    marker_palette=[color_curated[kk] for kk in leiden_isocortex],
                                    line_color="#464646")
fig.update_xaxes(tickfont=dict(size=20), tickangle=270)
fig.update_yaxes(title_font=dict(size=18), showticklabels=True, nticks=2, tickangle=270, title_standoff=0)
fig.update_layout(
    font_family="Arial",
    title=None,
    template='plotly_white', width=360, height=480, 
    showlegend=False,)
fig.update_annotations(font_family="Arial")
fig.write_image(f"./{trial_name}/plots/geneexp_isocortex.pdf")
fig.show()

/tmp/ipykernel_2750939/2966688448.py:5: ImplicitModificationWarning:

Trying to modify attribute `.obs` of view, initializing view as actual.



In [6]:
import scipy.stats as stats
greater_arr = []
for gg in gene_list:
    ggarr = []
    for ll in leiden_isocortex:
        s1 = adata_isocortex[adata_isocortex.obs['leiden'] ==ll, gg].X.A.squeeze().astype(np.float64)
        s2 = adata_isocortex[adata_isocortex.obs['leiden'] !=ll, gg].X.A.squeeze().astype(np.float64)
        _, pval = stats.ranksums(s1, s2, alternative="greater")
        if pval > 1e-6:
            ggarr.append(pval)
        else:
            ggarr.append("<1e-6")
    greater_arr.append(ggarr)
greater_arr = pd.DataFrame(greater_arr, columns=cat_isocortex, index=gene_list)
greater_arr.to_excel(f"./{trial_name}/outputs/geneexp_isocortex_ranksum_pval.xlsx")
greater_arr.to_latex(f"./{trial_name}/outputs/geneexp_isocortex_ranksum_pval.tex")
greater_arr

/tmp/ipykernel_2750939/63646348.py:16: FutureWarning:

In future versions `DataFrame.to_latex` is expected to utilise the base implementation of `Styler.to_latex` for formatting and rendering. The arguments signature may therefore change. It is recommended instead to use `DataFrame.style.to_latex` which also contains additional functionality.



L1   L2/3     L4        L5     L6       L6b       C28
Nrep       1.0  <1e-6  <1e-6     <1e-6    1.0       1.0     <1e-6
Ccn2       1.0    1.0    1.0  0.235231  <1e-6     <1e-6  0.999998
Rprm       1.0    1.0    1.0     <1e-6  <1e-6  0.955162       1.0
Fezf2      1.0    1.0    1.0     <1e-6  <1e-6     <1e-6   0.06056
Rorb     <1e-6    1.0  <1e-6       1.0    1.0       1.0       1.0
Rasgrf2    1.0  <1e-6  <1e-6       1.0    1.0       1.0       1.0
Gfap     <1e-6    1.0    1.0       1.0  <1e-6     <1e-6       1.0

In [7]:
name_dict = dict(zip(leiden_isocortex, cat_isocortex))
cluster = adata.obs["leiden"].apply(lambda x: "C28" if x=="28" else f"{name_dict[x]} ({x})" if x in leiden_isocortex else "others")
source = ColumnDataSource(dict(x=adata.obsm['spatial'][:, 0], y=-adata.obsm['spatial'][:, 1],
                                  rad=np.sqrt(adata.obs['cell_area'] / np.pi)*1.2,
                                  label=cluster))
p = figure(width=400, height=320, toolbar_location=None, match_aspect=True)
p.circle(
    'x', 'y', source=source,
    fill_color=factor_cmap('label', palette=[color_curated[x] for x in leiden_isocortex] + ["#bcbcbc"], 
                           factors=["C28" if x=="28" else f"{name_dict[x]} ({x})" for x in leiden_isocortex] + ["others"]),
    radius='rad', line_color=None,
    legend_group='label',
    )
p.legend.items = [p.legend.items[ii]  for ii in list(range(1, 6 + 1)) + [0] + [7] ]
p.outline_line_width = 0
p.axis.visible = False
p.grid.visible = False
p.title.text_font = "Arial"
p.legend.border_line_width = 2.
p.legend.border_line_color = "#030303"
p.legend.label_text_font = "Arial"
p.legend.label_text_font_size = '18px'
p.legend.glyph_height = 25
p.legend.glyph_width = 25
p.legend.label_height = 25
p.legend.nrows = 2
p.legend.location = (10, 10)
p.add_layout(p.legend[0], 'below')
p.match_aspect = True
show(p)

In [8]:
export_png(p, filename=f"{trial_name}/plots/show_isocortex.png")
p.output_backend = "svg"
export_svg(p, filename=f"{trial_name}/plots/show_isocortex.svg")

['trial-mouse_brain_coronal_Xenium_raw/plots/show_isocortex.svg']